# Project: Segmenting and Clustering Neighborhoods in Toronto

## This following scripts import data from web and store it in a dataframe

In [1]:
# import libraries
import pandas as pd
import numpy as np

### Import data from web page

In [2]:
# Webpage url                                                                                                               
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'

# Extract tables
dfs = pd.read_html(url)

# Get first table                                                                                                           
df = dfs[0]



### Clean up data and print the resultant shape

In [3]:
# Extract columns                                                                                                           
df2 = df[['Postal Code','Borough','Neighbourhood']]
print ('Initial shape:',df2.shape)

# remove rows with Borough = 'Not assigned'
df2 = df2[df2['Borough'] != 'Not assigned']
print ("Removing 'Borough' = 'Not assigned:",df2.shape)

# copy value from 'Borough' to 'Neighbourhood' if 'Borough' has a value but 'Neighbourhood' is 'Not assigned'
df2.loc[df2['Neighbourhood'] == 'Not assigned','Neighbourhood'] = df2['Borough']

# reset index
df2.reset_index(drop=True, inplace=True)
print(df2.head(10))

# print the resultant dataframe shape
df2.shape

Initial shape: (180, 3)
Removing 'Borough' = 'Not assigned: (103, 3)
  Postal Code           Borough                                Neighbourhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government
5         M9A         Etobicoke      Islington Avenue, Humber Valley Village
6         M1B       Scarborough                               Malvern, Rouge
7         M3B        North York                                    Don Mills
8         M4B         East York              Parkview Hill, Woodbine Gardens
9         M5B  Downtown Toronto                     Garden District, Ryerson


(103, 3)

### Now read Geospatial CSV

In [4]:
locationdf = pd.read_csv('http://cocl.us/Geospatial_data')
locationdf

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
..          ...        ...        ...
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

[103 rows x 3 columns]

### Here we expand the dataframe and adding lookup values
### corresponding to the lattitude and longitude based on postal code
### and update value of dataframe

In [5]:
# add columns
df2['Latitude']=0
df2['Longitude']=0

# loop through all postal codes
# lookup corresponding latitude and longitude

for ind in df2.index:
    item = locationdf[locationdf['Postal Code'] == df2.loc[ind,'Postal Code']]
    df2.loc[ind,'Latitude'] = item['Latitude'].to_numpy()
    df2.loc[ind,'Longitude'] = item['Longitude'].to_numpy()

df2



Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
..          ...               ...   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4          Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
..                                                 ...        ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100  Business reply mail Processing Centre, South C...  43.662744 -79.321558  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999  

[103 rows x 5 columns]

### Now import some libraries for create clusters and plots
### The below approach and codes are borrowed from Lab exercise of IBM Data Science Class for Machine Learning

In [6]:
# import libraries

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


### Find the coordinates of Toronto

In [7]:
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


### Create a visual map of Toronto and its borough

In [8]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighbourhood in zip(df2['Latitude'], df2['Longitude'], df2['Borough'], df2['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### Set up credentials for using Foursquare APIs

In [74]:
CLIENT_ID = 'NJNLFQFQ1JUVRMLQ2LLII5BM2XTUKWLNXEYAF2TGYBSLZRNY' # your Foursquare ID
CLIENT_SECRET = 'FZYI2S3POPHJMIZM0NZVY2KBEEUUSP0FC2YNZO4J2MKNRPGA' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: NJNLFQFQ1JUVRMLQ2LLII5BM2XTUKWLNXEYAF2TGYBSLZRNY
CLIENT_SECRET:FZYI2S3POPHJMIZM0NZVY2KBEEUUSP0FC2YNZO4J2MKNRPGA


### Explore first neighbourhood using Toronto neighbourhood dataframe

In [10]:
df2.loc[0, 'Neighbourhood']

'Parkwoods'

### Get neighbourhood details

In [11]:
neighbourhood_latitude = df2.loc[0, 'Latitude'] # neighbourhood latitude value
neighbourhood_longitude = df2.loc[0, 'Longitude'] # neighbourhood longitude value

neighbourhood_name = df2.loc[0, 'Neighbourhood'] # neighbourhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighbourhood_name, 
                                                               neighbourhood_latitude, 
                                                               neighbourhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


### Now get the top 100 venues that are in Parkwoods within a radius of 800 meters.
#### Note: If we use 500 meters, the number of venues returned will be just 3. We will get a warning from the API.

In [49]:
LIMIT=100
radius=800
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighbourhood_latitude, 
    neighbourhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=NJNLFQFQ1JUVRMLQ2LLII5BM2XTUKWLNXEYAF2TGYBSLZRNY&client_secret=FZYI2S3POPHJMIZM0NZVY2KBEEUUSP0FC2YNZO4J2MKNRPGA&v=20180605&ll=43.7532586,-79.3296565&radius=800&limit=100'

### Returned result set is in json format

In [50]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5fe2ca04f849016e7135a22e'},
 'response': {'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 5,
  'suggestedBounds': {'ne': {'lat': 43.76045860720001,
    'lng': -79.31970728375885},
   'sw': {'lat': 43.7460585928, 'lng': -79.33960571624115}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4e8d9dcdd5fbbbb6b3003c7b',
       'name': 'Brookbanks Park',
       'location': {'address': 'Toronto',
        'lat': 43.751976046055574,
        'lng': -79.33214044722958,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.751976046055574,
          'lng': -79.33214044722958}],
        'distance': 245,
        'cc': 'CA',

### Helper function for getting the category of the venue

In [51]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [52]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues

<ipython-input-52-4243e3e1ab9c>:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  nearby_venues = json_normalize(venues) # flatten JSON


name         categories        lat        lng
0    Brookbanks Park               Park  43.751976 -79.332140
1      Variety Store  Food & Drink Shop  43.751974 -79.333114
2  DVP at York Mills       Intersection  43.758899 -79.334099
3    TTC Stop #09083           Bus Stop  43.759655 -79.332223
4      TTC Stop 9083           Bus Stop  43.759251 -79.334000

In [53]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

5 venues were returned by Foursquare.


### Helper function for getting venues near by a latitude and longitude

In [54]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

### Since the Neighbourhood column contains one or more neighbours in one cell, we should split them up
### Then assign to a new dataframe

In [55]:
# create new dataframe by breaking down the neighbourhoods
df3 = pd.DataFrame(columns=['Postal Code', 'Borough', 'Neighbourhood', 'Latitude', 'Longitude'])
for ind in df2.index:
    l = df2.loc[ind, 'Neighbourhood'].split(", ")
    if len(l)>1:
        print (df2.loc[ind, 'Neighbourhood'].split(", "))
        for i in l:
            df3.loc[len(df3)] = df2.loc[ind,['Postal Code', 'Borough', 'Neighbourhood', 'Latitude', 'Longitude']]
            df3.loc[len(df3)-1,'Neighbourhood'] = i
    else:
        df3.loc[len(df3)] = df2.loc[ind,['Postal Code', 'Borough', 'Neighbourhood', 'Latitude', 'Longitude']]

df3

['Regent Park', 'Harbourfront']
['Lawrence Manor', 'Lawrence Heights']
["Queen's Park", 'Ontario Provincial Government']
['Islington Avenue', 'Humber Valley Village']
['Malvern', 'Rouge']
['Parkview Hill', 'Woodbine Gardens']
['Garden District', 'Ryerson']
['West Deane Park', 'Princess Gardens', 'Martin Grove', 'Islington', 'Cloverdale']
['Rouge Hill', 'Port Union', 'Highland Creek']
['Eringate', 'Bloordale Gardens', 'Old Burnhamthorpe', 'Markland Wood']
['Guildwood', 'Morningside', 'West Hill']
['Bathurst Manor', 'Wilson Heights', 'Downsview North']
['Richmond', 'Adelaide', 'King']
['Dufferin', 'Dovercourt Village']
['Fairview', 'Henry Farm', 'Oriole']
['Northwood Park', 'York University']
['East Toronto', 'Broadview North (Old East York)']
['Harbourfront East', 'Union Station', 'Toronto Islands']
['Little Portugal', 'Trinity']
['Kennedy Park', 'Ionview', 'East Birchmount Park']
['The Danforth West', 'Riverdale']
['Toronto Dominion Centre', 'Design Exchange']
['Brockton', 'Parkdale Vi

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M5A  Downtown Toronto   
4           M6A        North York   
5           M6A        North York   
6           M7A  Downtown Toronto   
7           M7A  Downtown Toronto   
8           M9A         Etobicoke   
9           M9A         Etobicoke   
10          M1B       Scarborough   
11          M1B       Scarborough   
12          M3B        North York   
13          M4B         East York   
14          M4B         East York   
15          M5B  Downtown Toronto   
16          M5B  Downtown Toronto   
17          M6B        North York   
18          M9B         Etobicoke   
19          M9B         Etobicoke   
20          M9B         Etobicoke   
21          M9B         Etobicoke   
22          M9B         Etobicoke   
23          M1C       Scarborough   
24          M1C       Scarborough   
25          M1C       Scarborough   
26          M3C        North York   
27          M4C         East York   
28          M5C  Downtown Toronto   
29          M6C              York   
30          M9C         Etobicoke   
31          M9C         Etobicoke   
32          M9C         Etobicoke   
33          M9C         Etobicoke   
34          M1E       Scarborough   
35          M1E       Scarborough   
36          M1E       Scarborough   
37          M4E      East Toronto   
38          M5E  Downtown Toronto   
39          M6E              York   
40          M1G       Scarborough   
41          M4G         East York   
42          M5G  Downtown Toronto   
43          M6G  Downtown Toronto   
44          M1H       Scarborough   
45          M2H        North York   
46          M3H        North York   
47          M3H        North York   
48          M3H        North York   
49          M4H         East York   
50          M5H  Downtown Toronto   
51          M5H  Downtown Toronto   
52          M5H  Downtown Toronto   
53          M6H      West Toronto   
54          M6H      West Toronto   
55          M1J       Scarborough   
56          M2J        North York   
57          M2J        North York   
58          M2J        North York   
59          M3J        North York   
60          M3J        North York   
61          M4J         East York   
62          M4J         East York   
63          M5J  Downtown Toronto   
64          M5J  Downtown Toronto   
65          M5J  Downtown Toronto   
66          M6J      West Toronto   
67          M6J      West Toronto   
68          M1K       Scarborough   
69          M1K       Scarborough   
70          M1K       Scarborough   
71          M2K        North York   
72          M3K        North York   
73          M4K      East Toronto   
74          M4K      East Toronto   
75          M5K  Downtown Toronto   
76          M5K  Downtown Toronto   
77          M6K      West Toronto   
78          M6K      West Toronto   
79          M6K      West Toronto   
80          M1L       Scarborough   
81          M1L       Scarborough   
82          M1L       Scarborough   
83          M2L        North York   
84          M2L        North York   
85          M3L        North York   
86          M4L      East Toronto   
87          M4L      East Toronto   
88          M5L  Downtown Toronto   
89          M5L  Downtown Toronto   
90          M6L        North York   
91          M6L        North York   
92          M6L        North York   
93          M9L        North York   
94          M1M       Scarborough   
95          M1M       Scarborough   
96          M1M       Scarborough   
97          M2M        North York   
98          M2M        North York   
99          M3M        North York   
100         M4M      East Toronto   
101         M5M        North York   
102         M5M        North York   
103         M6M              York   
104         M6M              York   
105         M6M              York   
106         M9M        North York   
107     

### We use the new dataframe to get a list of venues for each neighbourhood

In [57]:

toronto_venues = getNearbyVenues(names=df3['Neighbourhood'],
                                   latitudes=df3['Latitude'],
                                   longitudes=df3['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park
Harbourfront
Lawrence Manor
Lawrence Heights
Queen's Park
Ontario Provincial Government
Islington Avenue
Humber Valley Village
Malvern
Rouge
Don Mills
Parkview Hill
Woodbine Gardens
Garden District
Ryerson
Glencairn
West Deane Park
Princess Gardens
Martin Grove
Islington
Cloverdale
Rouge Hill
Port Union
Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate
Bloordale Gardens
Old Burnhamthorpe
Markland Wood
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Wilson Heights
Downsview North
Thorncliffe Park
Richmond
Adelaide
King
Dufferin
Dovercourt Village
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Broadview North (Old East York)
Harbourfront East
Union Station
Toronto Islands
Little Portugal
Trinity
Kennedy Park
Ionview
East Birchmount Park
Bayview Village
Downsvi

### We take a look at the shape of the data frames and all the returned venues in Toronto

In [58]:
print(toronto_venues.shape)
toronto_venues

(4326, 7)


Neighbourhood  Neighbourhood Latitude  \
0                                         Parkwoods               43.753259   
1                                         Parkwoods               43.753259   
2                                         Parkwoods               43.753259   
3                                  Victoria Village               43.725882   
4                                  Victoria Village               43.725882   
5                                  Victoria Village               43.725882   
6                                  Victoria Village               43.725882   
7                                  Victoria Village               43.725882   
8                                       Regent Park               43.654260   
9                                       Regent Park               43.654260   
10                                      Regent Park               43.654260   
11                                      Regent Park               43.654260   
12                                      Regent Park               43.654260   
13                                      Regent Park               43.654260   
14                                      Regent Park               43.654260   
15                                      Regent Park               43.654260   
16                                      Regent Park               43.654260   
17                                      Regent Park               43.654260   
18                                      Regent Park               43.654260   
19                                      Regent Park               43.654260   
20                                      Regent Park               43.654260   
21                                      Regent Park               43.654260   
22                                      Regent Park               43.654260   
23                                      Regent Park               43.654260   
24                                      Regent Park               43.654260   
25                                      Regent Park               43.654260   
26                                      Regent Park               43.654260   
27                                      Regent Park               43.654260   
28                                      Regent Park               43.654260   
29                                      Regent Park               43.654260   
30                                      Regent Park               43.654260   
31                                      Regent Park               43.654260   
32                                      Regent Park               43.654260   
33                                      Regent Park               43.654260   
34                                      Regent Park               43.654260   
35                                      Regent Park               43.654260   
36                                      Regent Park               43.654260   
37                                      Regent Park               43.654260   
38                                      Regent Park               43.654260   
39                                      Regent Park               43.654260   
40                                      Regent Park               43.654260   
41                                      Regent Park               43.654260   
42                                      Regent Park               43.654260   
43                                      Regent Park               43.654260   
44                                      Regent Park               43.654260   
45                                      Regent Park               43.654260   
46                                      Regent Park               43.654260   
47                                      Regent Park               43.654260   
48                                      Regent Park               43.654260   
49                                      Regent Park               43.654260   
50       

In [59]:
toronto_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                           
Adelaide                                                           96   
Agincourt                                                           4   
Agincourt North                                                     3   
Albion Gardens                                                     10   
Alderwood                                                           9   
Bathurst Manor                                                     22   
Bathurst Quay                                                      16   
Bayview Village                                                     4   
Beaumond Heights                                                   10   
Bedford Park                                                       23   
Berczy Park                                                        57   
Birch Cliff                                                         4   
Bloordale Gardens                                                   9   
Broadview North (Old East York)                                     3   
Brockton                                                           23   
Business reply mail Processing Centre                              16   
CN Tower                                                           16   
Cabbagetown                                                        46   
Caledonia-Fairbanks                                                 4   
Canada Post Gateway Processing Centre                              14   
Cedarbrae                                                           9   
Central Bay Street                                                 59   
Chinatown                                                          60   
Christie                                                           16   
Church and Wellesley                                               78   
Clairlea                                                           10   
Clarks Corners                                                     14   
Cliffcrest                                                          4   
Cliffside                                                           4   
Cliffside West                                                      4   
Cloverdale                                                          1   
Commerce Court                                                    100   
Davisville                                                         35   
Davisville North                                                    9   
Deer Park                                                          14   
Del Ray                                                             4   
Design Exchange                                                   100   
Don Mills                                                          26   
Dorset Park                                                         6   
Dovercourt Village                                                 14   
Downsview                                                          14   
Downsview North                                                    22   
Dufferin                                                           14   
East Birchmount Park                                                5   
East Toronto                                                        3   
Emery                                                               2   
Eringate                                                            9   
Exhibition Place                                                   23   
Fairview                                                           71   
First Canadian Place                                              100   
Forest Hill North & West                                            5   
Forest Hill Road Park                                               5   
Forest Hill SE                                                     14   
Garden District                 

In [60]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 268 uniques categories.


### Now we create a matrix containing onehot encoding of the venues
### and group them into another dataframe

In [61]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Accessories Store  Adult Boutique  Airport  \
0         Parkwoods                  0               0        0   
1         Parkwoods                  0               0        0   
2         Parkwoods                  0               0        0   
3  Victoria Village                  0               0        0   
4  Victoria Village                  0               0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       0   
2            0              0          0           0           0       0   
3            0              0          0           0           0       0   
4            0              0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0     0    0               0                 0                   0      0   
1     0    0               0                 0                   0      0   
2     0    0               0                 0                   0      0   
3     0    0               0                 0                   0      0   
4     0    0               0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0       0           0              0          0         0   
1       0           0              0          0         0   
2       0           0              0          0         0   
3       0           0              0          0         0   
4       0           0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0        

In [62]:
toronto_onehot.shape

(4326, 269)

In [63]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood  Accessories Store  \
0                                         Adelaide           0.000000   
1                                        Agincourt           0.000000   
2                                  Agincourt North           0.000000   
3                                   Albion Gardens           0.000000   
4                                        Alderwood           0.000000   
5                                   Bathurst Manor           0.000000   
6                                    Bathurst Quay           0.000000   
7                                  Bayview Village           0.000000   
8                                 Beaumond Heights           0.000000   
9                                     Bedford Park           0.000000   
10                                     Berczy Park           0.000000   
11                                     Birch Cliff           0.000000   
12                               Bloordale Gardens           0.000000   
13                 Broadview North (Old East York)           0.000000   
14                                        Brockton           0.000000   
15           Business reply mail Processing Centre           0.000000   
16                                        CN Tower           0.000000   
17                                     Cabbagetown           0.000000   
18                             Caledonia-Fairbanks           0.000000   
19           Canada Post Gateway Processing Centre           0.000000   
20                                       Cedarbrae           0.000000   
21                              Central Bay Street           0.000000   
22                                       Chinatown           0.000000   
23                                        Christie           0.000000   
24                            Church and Wellesley           0.000000   
25                                        Clairlea           0.000000   
26                                  Clarks Corners           0.000000   
27                                      Cliffcrest           0.000000   
28                                       Cliffside           0.000000   
29                                  Cliffside West           0.000000   
30                                      Cloverdale           0.000000   
31                                  Commerce Court           0.000000   
32                                      Davisville           0.000000   
33                                Davisville North           0.000000   
34                                       Deer Park           0.000000   
35                                         Del Ray           0.000000   
36                                 Design Exchange           0.000000   
37                                       Don Mills           0.000000   
38                                     Dorset Park           0.000000   
39                              Dovercourt Village           0.000000   
40                                       Downsview           0.000000   
41                                 Downsview North           0.000000   
42                                        Dufferin           0.000000   
43                            East Birchmount Park           0.000000   
44                                    East Toronto           0.000000   
45                                           Emery           0.000000   
46                                        Eringate           0.000000   
47                                Exhibition Place           0.000000   
48                                        Fairview           0.000000   
49                            First Canadian Place           0.000000   
50                        Forest Hill North & West           0.000000   
51                           Forest Hill Road Park           0.000000   
52                                  Forest Hill SE           0.000000   
53                                 Garden District           0.000000   
54                    

In [64]:
toronto_grouped.shape

(203, 269)

In [65]:
num_top_venues = 5

for hood in toronto_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
         venue  freq
0  Coffee Shop  0.10
1         Café  0.05
2   Restaurant  0.04
3          Gym  0.03
4        Hotel  0.03


----Agincourt----
                       venue  freq
0             Clothing Store  0.25
1                     Lounge  0.25
2             Breakfast Spot  0.25
3  Latin American Restaurant  0.25
4         Miscellaneous Shop  0.00


----Agincourt North----
          venue  freq
0    Playground  0.33
1          Park  0.33
2  Intersection  0.33
3     Pet Store  0.00
4         Motel  0.00


----Albion Gardens----
           venue  freq
0  Grocery Store   0.2
1    Pizza Place   0.1
2    Video Store   0.1
3       Pharmacy   0.1
4     Beer Store   0.1


----Alderwood----
                venue  freq
0         Pizza Place  0.22
1                 Pub  0.11
2        Skating Rink  0.11
3      Sandwich Place  0.11
4  Athletics & Sports  0.11


----Bathurst Manor----
                       venue  freq
0                Coffee Shop  0.09
1                      

4  Furniture / Home Store  0.08


----Lawrence Heights----
                    venue  freq
0          Clothing Store  0.23
1  Furniture / Home Store  0.15
2       Accessories Store  0.08
3             Coffee Shop  0.08
4             Event Space  0.08


----Lawrence Manor----
                    venue  freq
0          Clothing Store  0.23
1  Furniture / Home Store  0.15
2       Accessories Store  0.08
3             Coffee Shop  0.08
4             Event Space  0.08


----Lawrence Manor East----
                venue  freq
0         Coffee Shop  0.09
1      Sandwich Place  0.09
2  Italian Restaurant  0.09
3   Indian Restaurant  0.04
4             Butcher  0.04


----Lawrence Park----
            venue  freq
0  Clothing Store  0.14
1            Park  0.09
2     Coffee Shop  0.09
3     Yoga Studio  0.05
4           Diner  0.05


----Leaside----
                    venue  freq
0             Coffee Shop  0.09
1     Sporting Goods Shop  0.09
2  Furniture / Home Store  0.06
3           Shopping

                  venue  freq
0            Kids Store  0.07
1        Sandwich Place  0.07
2  Fast Food Restaurant  0.07
3           Wings Joint  0.07
4        Hardware Store  0.07


----Thistletown----
           venue  freq
0  Grocery Store   0.2
1    Pizza Place   0.1
2    Video Store   0.1
3       Pharmacy   0.1
4     Beer Store   0.1


----Thorncliffe Park----
               venue  freq
0  Indian Restaurant  0.10
1        Yoga Studio  0.05
2        Gas Station  0.05
3        Pizza Place  0.05
4               Park  0.05


----Toronto Dominion Centre----
         venue  freq
0  Coffee Shop  0.11
1        Hotel  0.07
2         Café  0.06
3  Salad Place  0.04
4   Restaurant  0.04


----Toronto Islands----
                venue  freq
0         Coffee Shop  0.13
1            Aquarium  0.05
2                Café  0.04
3               Hotel  0.04
4  Italian Restaurant  0.03


----Trinity----
                   venue  freq
0                    Bar  0.09
1       Asian Restaurant  0.05
2     

In [66]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [67]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue      2nd Most Common Venue  \
0         Adelaide           Coffee Shop                       Café   
1        Agincourt                Lounge  Latin American Restaurant   
2  Agincourt North          Intersection                 Playground   
3   Albion Gardens         Grocery Store                   Pharmacy   
4        Alderwood           Pizza Place                   Pharmacy   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Restaurant                   Gym       Thai Restaurant   
1        Breakfast Spot        Clothing Store           Event Space   
2                  Park      Doner Restaurant          Dessert Shop   
3           Video Store   Japanese Restaurant        Sandwich Place   
4    Athletics & Sports           Coffee Shop                   Pub   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Deli / Bodega                 Hotel            Steakhouse   
1  Ethiopian Restaurant    Falafel Restaurant           Escape Room   
2    Dim Sum Restaurant                 Diner        Discount Store   
3            Beer Store   Fried Chicken Joint  Fast Food Restaurant   
4        Sandwich Place          Skating Rink                   Gym   

  9th Most Common Venue       10th Most Common Venue  
0        Clothing Store                       Bakery  
1                 Diner            Electronics Store  
2   Distribution Center                      Dog Run  
3           Pizza Place  Eastern European Restaurant  
4      Airport Terminal         Colombian Restaurant

### Perform a KMeans clustering and assign a cluster label to each of the grouped neighbourhood

In [68]:
# set number of clusters
kclusters = 30

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([ 1,  1, 15,  7, 12, 12, 24,  1,  7,  1], dtype=int32)

In [69]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df3

# merge toronto_grouped with df2 to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

toronto_merged.head(10) # check the last columns!

Postal Code           Borough                  Neighbourhood   Latitude  \
0         M3A        North York                      Parkwoods  43.753259   
1         M4A        North York               Victoria Village  43.725882   
2         M5A  Downtown Toronto                    Regent Park  43.654260   
3         M5A  Downtown Toronto                   Harbourfront  43.654260   
4         M6A        North York                 Lawrence Manor  43.718518   
5         M6A        North York               Lawrence Heights  43.718518   
6         M7A  Downtown Toronto                   Queen's Park  43.662301   
7         M7A  Downtown Toronto  Ontario Provincial Government  43.662301   
8         M9A         Etobicoke               Islington Avenue  43.667856   
9         M9A         Etobicoke          Humber Valley Village  43.667856   

   Longitude  Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
0 -79.329656            25.0  Fast Food Restaurant       Food & Drink Shop   
1 -79.315572             1.0           Pizza Place             Coffee Shop   
2 -79.360636             1.0           Coffee Shop                  Bakery   
3 -79.360636             1.0           Coffee Shop                  Bakery   
4 -79.464763             1.0        Clothing Store  Furniture / Home Store   
5 -79.464763             1.0        Clothing Store  Furniture / Home Store   
6 -79.389494             1.0           Coffee Shop        Sushi Restaurant   
7 -79.389494             1.0           Coffee Shop        Sushi Restaurant   
8 -79.532242             NaN                   NaN                     NaN   
9 -79.532242             NaN                   NaN                     NaN   

  3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0                  Park                  Diner        Discount Store   
1     French Restaurant  Portuguese Restaurant          Hockey Arena   
2                  Park                   Café                   Pub   
3                  Park                   Café                   Pub   
4     Accessories Store               Boutique             Gift Shop   
5     Accessories Store               Boutique             Gift Shop   
6                  Park                    Bar              Beer Bar   
7                  Park                    Bar              Beer Bar   
8                   NaN                    NaN                   NaN   
9                   NaN                    NaN                   NaN   

  6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
0   Distribution Center                      Dog Run      Doner Restaurant   
1     Electronics Store  Eastern European Restaurant           Escape Room   
2        Breakfast Spot                      Theater                   Spa   
3        Breakfast Spot                      Theater                   Spa   
4           Event Space           Miscellaneous Shop           Coffee Shop   
5           Event Space           Miscellaneous Shop           Coffee Shop   
6         Smoothie Shop               Sandwich Place         Burrito Place   
7         Smoothie Shop               Sandwich Place         Burrito Place   
8                   NaN                          NaN                   NaN   
9                   NaN                          NaN                   NaN   

  9th Most Common Venue 10th Most Common Venue  
0            Donut Shop              Drugstore  
1             Drugstore       Department Store  
2            Shoe Store                Brewery  
3            Shoe Store                Brewery  
4         Women's Store  Vietnamese Restaurant  
5         Women's Store  Vietnamese Restaurant  
6            Restaurant                   Café  
7            Restaurant                   Café  
8                   NaN                    NaN  
9                   NaN                    NaN

In [70]:
# clean up of data
# drop those items with NAN

toronto_merged.dropna(inplace=True)
toronto_merged = toronto_merged.astype({"Cluster Labels": int})
toronto_merged['Cluster Labels']

0      25
1       1
2       1
3       1
4       1
5       1
6       1
7       1
10     18
11     18
12      1
13     12
14     12
15      1
16      1
17     12
18      3
19      3
20      3
21      3
22      3
23      5
24      5
25      5
26      1
27     12
28      1
29      1
30     12
31     12
32     12
33     12
34      1
35      1
36      1
37      1
38      1
39      9
40     22
41      1
42      1
43     12
44      1
45      1
46     12
47     12
48     12
49     12
50      1
51      1
52      1
53     12
54     12
55     26
56      1
57      1
58      1
59      1
60      1
61     14
62     14
63      1
64      1
65      1
66      1
67      1
68     20
69     20
70     20
71      1
72     12
73      1
74      1
75      1
76      1
77      1
78      1
79      1
80     23
81     23
82     23
85     12
86     12
87     12
88      1
89      1
90     17
91     17
92     17
93     19
94     10
95     10
96     10
97     12
98     14
99     12
100     1
101     1
102     1
103     8


### Create a visual map of clusters in Toronto

In [71]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Examine the clusters

### Cluster 1

In [72]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels      1st Most Common Venue  \
128  Scarborough               0  Middle Eastern Restaurant   
129  Scarborough               0  Middle Eastern Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
128           Auto Garage            Smoke Shop                Bakery   
129           Auto Garage            Smoke Shop                Bakery   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
128         Shopping Mall        Sandwich Place      Doner Restaurant   
129         Shopping Mall        Sandwich Place      Doner Restaurant   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
128        Discount Store   Distribution Center                Dog Run  
129        Discount Store   Distribution Center                Dog Run

### Cluster 2

In [73]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels   1st Most Common Venue  \
1          North York               1             Pizza Place   
2    Downtown Toronto               1             Coffee Shop   
3    Downtown Toronto               1             Coffee Shop   
4          North York               1          Clothing Store   
5          North York               1          Clothing Store   
6    Downtown Toronto               1             Coffee Shop   
7    Downtown Toronto               1             Coffee Shop   
12         North York               1                     Gym   
15   Downtown Toronto               1             Coffee Shop   
16   Downtown Toronto               1             Coffee Shop   
26         North York               1                     Gym   
28   Downtown Toronto               1             Coffee Shop   
29               York               1                   Field   
34        Scarborough               1            Intersection   
35        Scarborough               1            Intersection   
36        Scarborough               1            Intersection   
37       East Toronto               1            Neighborhood   
38   Downtown Toronto               1             Coffee Shop   
41          East York               1             Coffee Shop   
42   Downtown Toronto               1             Coffee Shop   
44        Scarborough               1        Hakka Restaurant   
45         North York               1             Golf Course   
50   Downtown Toronto               1             Coffee Shop   
51   Downtown Toronto               1             Coffee Shop   
52   Downtown Toronto               1             Coffee Shop   
56         North York               1          Clothing Store   
57         North York               1          Clothing Store   
58         North York               1          Clothing Store   
59         North York               1  Furniture / Home Store   
60         North York               1  Furniture / Home Store   
63   Downtown Toronto               1             Coffee Shop   
64   Downtown Toronto               1             Coffee Shop   
65   Downtown Toronto               1             Coffee Shop   
66       West Toronto               1                     Bar   
67       West Toronto               1                     Bar   
71         North York               1                    Café   
73       East Toronto               1        Greek Restaurant   
74       East Toronto               1        Greek Restaurant   
75   Downtown Toronto               1             Coffee Shop   
76   Downtown Toronto               1             Coffee Shop   
77       West Toronto               1                    Café   
78       West Toronto               1                    Café   
79       West Toronto               1                    Café   
88   Downtown Toronto               1             Coffee Shop   
89   Downtown Toronto               1             Coffee Shop   
100      East Toronto               1             Coffee Shop   
101        North York               1             Coffee Shop   
102        North York               1             Coffee Shop   
113   Central Toronto               1          Clothing Store   
114   Central Toronto               1                  Garden   
125      West Toronto               1           Grocery Store   
126      West Toronto               1           Grocery Store   
132   Central Toronto               1          Clothing Store   
133   Central Toronto               1          Clothing Store   
137      West Toronto               1          Breakfast Spot   
138      West Toronto               1          Breakfast Spot   
139       Mississauga               1             Coffee Shop   
144       Scarborough               1                  Lounge   
146  Downtown Toronto               1                    Café   
147  Downtown Toronto               1                    Café   
149      West Toronto               1            